# Dataset Annoteren met Getraind Yolo-V8(n) Model

In [1]:
import os
import cv2
import pandas as pd
import shutil
from tqdm.notebook import tqdm
from ultralytics import YOLO

# Laad de annotaties
annotations = pd.read_csv('D4.1.2_auto_annotations.csv')

# Normaliseer de coördinaten
def normalize_coordinates(row, img_width, img_height):
    row['x_center'] = row['x_center'] / img_width
    row['y_center'] = row['y_center'] / img_height
    row['width'] = row['width'] / img_width
    row['height'] = row['height'] / img_height
    return row

# Validatie om ervoor te zorgen dat coördinaten genormaliseerd zijn
def validate_normalized_coordinates(row):
    if not (0 <= row['x_center'] <= 1 and 0 <= row['y_center'] <= 1 and 0 <= row['width'] <= 1 and 0 <= row['height'] <= 1):
        raise ValueError(f"Invalid normalized coordinates: {row}")

# Normaliseer de annotaties
valid_annotations = []
for idx, row in annotations.iterrows():
    image_path = os.path.join('Data/images_resized', row['image_name'])
    image = cv2.imread(image_path)
    if image is not None:
        img_height, img_width, _ = image.shape
        row = normalize_coordinates(row, img_width, img_height)
        try:
            validate_normalized_coordinates(row)
            valid_annotations.append(row)
        except ValueError as e:
            print(f"Skipping invalid annotation for image {row['image_name']}: {e}")

In [2]:
# Zet de geldige annotaties om in een DataFrame en sla op als CSV
valid_annotations_df = pd.DataFrame(valid_annotations)
valid_annotations_df.to_csv('D4.1.2_auto_annotations_normalized.csv', index=False)

# Splits de annotaties in YOLO formaat
def prepare_yolo_data(annotations, images_folder, output_folder):
    os.makedirs(output_folder, exist_ok=True)
    for _, row in annotations.iterrows():
        image_path = os.path.join(images_folder, row['image_name'])
        image = cv2.imread(image_path)
        if image is None:
            continue
        h, w, _ = image.shape
        label_path = os.path.join(output_folder, f"{os.path.splitext(row['image_name'])[0]}.txt")
        with open(label_path, 'w') as f:
            f.write(f"0 {row['x_center']} {row['y_center']} {row['width']} {row['height']}\n")

# Maak de benodigde directories aan
os.makedirs('Data/train/images', exist_ok=True)
os.makedirs('Data/train/labels', exist_ok=True)
os.makedirs('Data/val/images', exist_ok=True)
os.makedirs('Data/val/labels', exist_ok=True)

# Laad de genormaliseerde annotaties
annotations = pd.read_csv('D4.1.2_auto_annotations_normalized.csv')

In [3]:
# Split de data in training en validatie sets
train_annotations = annotations.sample(frac=0.8, random_state=42)
val_annotations = annotations.drop(train_annotations.index)

# Kopieer de afbeeldingen naar de juiste mappen en maak de YOLO annotaties
prepare_yolo_data(train_annotations, 'Data/images_resized', 'Data/train/labels')
prepare_yolo_data(val_annotations, 'Data/images_resized', 'Data/val/labels')

# Kopieer de afbeeldingen naar de train en val mappen
for img_name in train_annotations['image_name']:
    shutil.copy(os.path.join('Data/images_resized', img_name), 'Data/train/images')

for img_name in val_annotations['image_name']:
    shutil.copy(os.path.join('Data/images_resized', img_name), 'Data/val/images')

In [4]:


# YAML-configuratiebestand aanmaken
dataset_yaml_content = """
train: C:/Users/Gebruiker/Documents/Fontys/S6 - AI/Personal - Data Driven Challenge/Dopsis Detection/Data/train/images
val: C:/Users/Gebruiker/Documents/Fontys/S6 - AI/Personal - Data Driven Challenge/Dopsis Detection/Data/val/images

nc: 1
names: ['Insect']
"""

with open('D4.1.2_Yolo_Model_Dataset.yaml', 'w') as f:
    f.write(dataset_yaml_content)

In [5]:
# Train het YOLOv8 model met voortgangsweergave
model = YOLO('yolov8n.yaml')

# Train het model met early stopping
model.train(data='D4.1.2_Yolo_Model_Dataset.yaml', epochs=15, batch=16, imgsz=128)

New https://pypi.org/project/ultralytics/8.2.32 available  Update with 'pip install -U ultralytics'
Ultralytics YOLOv8.2.31  Python-3.11.1 torch-2.2.2+cpu CPU (AMD Ryzen 7 5700U with Radeon Graphics)
engine\trainer: task=detect, mode=train, model=yolov8n.yaml, data=D4.1.2_Yolo_Model_Dataset.yaml, epochs=15, time=None, patience=100, batch=16, imgsz=128, save=True, save_period=-1, cache=False, device=None, workers=8, project=None, name=train9, exist_ok=False, pretrained=True, optimizer=auto, verbose=True, seed=0, deterministic=True, single_cls=False, rect=False, cos_lr=False, close_mosaic=10, resume=False, amp=True, fraction=1.0, profile=False, freeze=None, multi_scale=False, overlap_mask=True, mask_ratio=4, dropout=0.0, val=True, split=val, save_json=False, save_hybrid=False, conf=None, iou=0.7, max_det=300, half=False, dnn=False, plots=True, source=None, vid_stride=1, stream_buffer=False, visualize=False, augment=False, agnostic_nms=False, classes=None, retina_masks=False, embed=None, 

train: Scanning C:\Users\Gebruiker\Documents\Fontys\S6 - AI\Personal - Data Driven Challenge\Dopsis Detection\Data\train\labels.cache... 36171 images, 0 backgrounds, 7234 corrupt: 100%|██████████| 36171/36171 [00:00<?, ?it/s]

train: WARNING  C:\Users\Gebruiker\Documents\Fontys\S6 - AI\Personal - Data Driven Challenge\Dopsis Detection\Data\train\images\102_20200628004052_18637.jpg: ignoring corrupt image/label: non-normalized or out of bounds coordinates [      61.81      68.292      57.012      62.571]
train: WARNING  C:\Users\Gebruiker\Documents\Fontys\S6 - AI\Personal - Data Driven Challenge\Dopsis Detection\Data\train\images\102_20200628004052_18645.jpg: ignoring corrupt image/label: non-normalized or out of bounds coordinates [     83.421      50.148      70.457      74.723]
train: WARNING  C:\Users\Gebruiker\Documents\Fontys\S6 - AI\Personal - Data Driven Challenge\Dopsis Detection\Data\train\images\102_20200628004151_9474.jpg: ignoring corrupt image/label: non-normalized or out of bounds coordinates [     60.459      62.037      60.633      65.146]
train: WARNING  C:\Users\Gebruiker\Documents\Fontys\S6 - AI\Personal - Data Driven Challenge\Dopsis Detection\Data\train\images\102_20200628004151_9476.jpg


val: Scanning C:\Users\Gebruiker\Documents\Fontys\S6 - AI\Personal - Data Driven Challenge\Dopsis Detection\Data\val\labels.cache... 14469 images, 0 backgrounds, 7235 corrupt: 100%|██████████| 14469/14469 [00:00<?, ?it/s]

val: WARNING  C:\Users\Gebruiker\Documents\Fontys\S6 - AI\Personal - Data Driven Challenge\Dopsis Detection\Data\val\images\102_20200628004052_18640.jpg: ignoring corrupt image/label: non-normalized or out of bounds coordinates [     60.131      53.033      65.588      67.579]
val: WARNING  C:\Users\Gebruiker\Documents\Fontys\S6 - AI\Personal - Data Driven Challenge\Dopsis Detection\Data\val\images\102_20200628004052_18642.jpg: ignoring corrupt image/label: non-normalized or out of bounds coordinates [     55.894      60.657      65.953      62.693]
val: WARNING  C:\Users\Gebruiker\Documents\Fontys\S6 - AI\Personal - Data Driven Challenge\Dopsis Detection\Data\val\images\102_20200628004052_18643.jpg: ignoring corrupt image/label: non-normalized or out of bounds coordinates [     70.393      78.028      69.913      75.228]
val: WARNING  C:\Users\Gebruiker\Documents\Fontys\S6 - AI\Personal - Data Driven Challenge\Dopsis Detection\Data\val\images\102_20200628004151_9471.jpg: ignoring corr

...

                   all       7234       7234      0.986      0.991      0.994      0.718



15 epochs completed in 4.574 hours.
Optimizer stripped from runs\detect\train9\weights\last.pt, 6.2MB
Optimizer stripped from runs\detect\train9\weights\best.pt, 6.2MB

Validating runs\detect\train9\weights\best.pt...
Ultralytics YOLOv8.2.31  Python-3.11.1 torch-2.2.2+cpu CPU (AMD Ryzen 7 5700U with Radeon Graphics)
YOLOv8n summary (fused): 168 layers, 3005843 parameters, 0 gradients, 8.1 GFLOPs


                 Class     Images  Instances      Box(P          R      mAP50  mAP50-95): 100%|██████████| 227/227 [02:13<00:00,  1.69it/s]


                   all       7234       7234      0.987      0.991      0.994      0.717
Speed: 0.2ms preprocess, 15.5ms inference, 0.0ms loss, 0.2ms postprocess per image
Results saved to runs\detect\train9


ultralytics.utils.metrics.DetMetrics object with attributes:

ap_class_index: array([0])
box: ultralytics.utils.metrics.Metric object
confusion_matrix: <ultralytics.utils.metrics.ConfusionMatrix object at 0x000001CA2F7EE2D0>
curves: ['Precision-Recall(B)', 'F1-Confidence(B)', 'Precision-Confidence(B)', 'Recall-Confidence(B)']
curves_results: [[array([          0,    0.001001,    0.002002,    0.003003,    0.004004,    0.005005,    0.006006,    0.007007,    0.008008,    0.009009,     0.01001,    0.011011,    0.012012,    0.013013,    0.014014,    0.015015,    0.016016,    0.017017,    0.018018,    0.019019,     0.02002,    0.021021,    0.022022,    0.023023,
          0.024024,    0.025025,    0.026026,    0.027027,    0.028028,    0.029029,     0.03003,    0.031031,    0.032032,    0.033033,    0.034034,    0.035035,    0.036036,    0.037037,    0.038038,    0.039039,     0.04004,    0.041041,    0.042042,    0.043043,    0.044044,    0.045045,    0.046046,    0.047047,
          0.0480

In [8]:
# Exporteer het model als TorchScript-bestand
model.export(format='torchscript')

Ultralytics YOLOv8.2.31  Python-3.11.1 torch-2.2.2+cpu CPU (AMD Ryzen 7 5700U with Radeon Graphics)
YOLOv8n summary (fused): 168 layers, 3005843 parameters, 0 gradients, 8.1 GFLOPs

PyTorch: starting from 'runs\detect\train9\weights\best.pt' with input shape (1, 3, 128, 128) BCHW and output shape(s) (1, 5, 336) (5.9 MB)

TorchScript: starting export with torch 2.2.2+cpu...
TorchScript: export success  1.4s, saved as 'runs\detect\train9\weights\best.torchscript' (11.8 MB)

Export complete (3.3s)
Results saved to C:\Users\Gebruiker\Documents\Fontys\S6 - AI\Personal - Data Driven Challenge\Dopsis Detection\runs\detect\train9\weights
Predict:         yolo predict task=detect model=runs\detect\train9\weights\best.torchscript imgsz=128  
Validate:        yolo val task=detect model=runs\detect\train9\weights\best.torchscript imgsz=128 data=D4.1.2_Yolo_Model_Dataset.yaml  
Visualize:       https://netron.app


'runs\\detect\\train9\\weights\\best.torchscript'